# 기본 설정

In [1]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt

%matplotlib inline

import json
import folium

In [2]:
# 한글 문제
import platform

from matplotlib import font_manager, rc
plt.rcParams['axes.unicode_minus'] = False

if platform.system() == 'Darwin':  # 맥OS 
    rc('font', family='AppleGothic')
elif platform.system() == 'Windows':  # 윈도우
    path = "c:/Windows/Fonts/malgun.ttf"
    font_name = font_manager.FontProperties(fname=path).get_name()
    rc('font', family=font_name)
else:
    print('Unknown system...  sorry~~~')

## 데이터 불러오기

In [3]:
region = pd.read_csv("../data/region.csv", encoding="utf-8")
region.head()

지역      주민등록인구  심장질환사망자  심장장애  상급종합병원  종합병원   병원  심장혈관흉부외과의원   일반의  \
0    강원도   1538492.0   4900.0   121       2    13   37         1.0   220   
1    경기도  13565450.0  25708.0  1295       5    62  277         9.0  1039   
2   경상남도   3314183.0  10312.0   268       3    23  134         2.0   420   
3   경상북도   2626609.0   9880.0   311       0    20   55         2.0   404   
4  광주광역시   1441611.0   2712.0   140       2    21   84         0.0   148   

     전문의    간호사  임상병리사  심장혈관흉부외과전문의   입원병상   입원병실  중환병상  중환병실  구급차  구급대원  
0   2211   6622    661           36   2398   8403    53   438  128  1014  
1  19686  46768   5526          209  13890  48092   226  2209  261  1896  
2   4856  14959   1829           72   6636  22556    50   555  139  1194  
3   3167  10143    988           51   3458  11404    49   495  146  1279  
4   3092   9414    941           33   4427  13894    27   408   30   270

# 함수
geojson 출처: https://cartographyvectors.com/map/1516-south-korea-with-regions

In [4]:
def chroplethmap(data, col, color, path=None):
    
    with open("../data/south-korea-with-regions_1516.geojson", "r", encoding="UTF-8") as f:
        geo_json = json.load(f)
    
    korea_map = folium.Map(location=[36.36109, 127.79209], zoom_start=6)

    fmap = folium.Choropleth(geo_data=geo_json,
                             data=data,
                             columns=["지역", col],
                             key_on="feature.properties.name",
                             fill_color=color,
                             legend_name=col).add_to(korea_map)

    fmap.geojson.zoom_on_click = False
    fmap.geojson.add_child(folium.features.GeoJsonTooltip(["name"],labels=False))
    display(korea_map)
    
    if path:
        korea_map.save(path)

# 지역별 전체 시각화

In [5]:
for col in region.columns[1:]:
    print(f"{'='*30}\n{col}\n{'='*30}")
    chroplethmap(region, col, "PuBu")

주민등록인구


심장질환사망자


심장장애


상급종합병원


종합병원


...

입원병실


중환병상


중환병실


구급차


구급대원


# 지역별 인구비례

In [7]:
# 인구 10만명 단위
pop_100000 = region["주민등록인구"] // 100000

# 주민등록인구 제거
region_pop = region.drop(["주민등록인구"], axis=1, inplace=False)

# 지역 뺀 컬럼리스트
col_list = list(region_pop)
col_list.remove("지역")

# 10만명 당 변수
region_pop[col_list] = region_pop[col_list].apply(lambda x: x / pop_100000)

In [8]:
for col in region_pop.columns[1:]:
    print(f"{'='*30}\n{col}\n{'='*30}")
    chroplethmap(region_pop, col, "YlGn")

심장질환사망자


심장장애


상급종합병원


종합병원


병원


...

입원병실


중환병상


중환병실


구급차


구급대원
